In [1]:
import tensorflow as tf
import numpy as np
import json
import os

/Users/hotamul/.pyenv/versions/gns-torch/lib/python3.11/site-packages/keras/src/export/tf2onnx_lib.py:8: FutureWarning: In the future `np.object` will be defined as the corresponding NumPy scalar.
  if not hasattr(np, "object"):


In [2]:
dataset_name = 'Sand'
data_path = f'./datasets/{dataset_name}'

for split in ['train', 'test', 'valid']:
    tfrecord_path = os.path.join(data_path, f'{split}.tfrecord')
    metadata_path = os.path.join(data_path, 'metadata.json')
    
    output_dir = os.path.join(data_path, split)
    os.makedirs(output_dir, exist_ok=True)
    
    with open(metadata_path, 'r') as f:
        metadata = json.load(f)
    
    with open(os.path.join(output_dir, 'metadata.json'), 'w') as f:
        json.dump(metadata, f)
    
    def parse_serialized_simulation(example_proto):
        context_features = {
            'particle_type': tf.io.VarLenFeature(tf.string),
            'key': tf.io.VarLenFeature(tf.int64)
        }
        sequence_features = {
            'position': tf.io.VarLenFeature(tf.string),
        }
        context, sequence = tf.io.parse_single_sequence_example(
            example_proto, context_features, sequence_features
        )
        particle_type = tf.io.decode_raw(tf.sparse.to_dense(context['particle_type']), tf.int64)
        position = tf.io.decode_raw(tf.sparse.to_dense(sequence['position']), tf.float32)
        key = tf.sparse.to_dense(context['key'])
        return position, particle_type, key
    
    raw_dataset = tf.data.TFRecordDataset(tfrecord_path, compression_type=None)
    
    print(f"=== Converting {dataset_name} to individual .npz files ===")
    print(f"Output Directory: {output_dir}")
    
    for i, raw_record in enumerate(raw_dataset):
        try:
            pos_raw, type_raw, key_raw = parse_serialized_simulation(raw_record)
            
            pos_np = pos_raw.numpy()
            type_np = type_raw.numpy()
            key_np = key_raw.numpy()
            
            if pos_np.ndim == 3 and pos_np.shape[1] == 1:
                pos_np = np.squeeze(pos_np, axis=1)
                
            dim = metadata['dim']
            seq_length = pos_np.shape[0]
            num_particles = pos_np.shape[1] // dim
            
            final_pos = pos_np.reshape(seq_length, num_particles, dim)
            final_type = type_np.flatten()
            final_key = key_np[0] if key_np.size > 0 else i
            
            save_name = os.path.join(output_dir, f"trajectory_{i:04d}.npz")
            
            np.savez_compressed(
                save_name,
                position=final_pos,
                particle_type=final_type,
                key=final_key
            )
            
            if (i+1) % 10 == 0:
                print(f"... Saved {i+1} files")
                
        except Exception as e:
            print(f"Error at index {i}: {e}")

2026-01-10 14:57:42.635758: I tensorflow/core/kernels/data/tf_record_dataset_op.cc:390] TFRecordDataset `buffer_size` is unspecified, default to 262144


=== Converting Sand to individual .npz files ===
Output Directory: ./datasets/Sand/train
... Saved 10 files
... Saved 20 files
... Saved 30 files
... Saved 40 files
... Saved 50 files
... Saved 60 files
... Saved 70 files
... Saved 80 files
... Saved 90 files
... Saved 100 files
... Saved 110 files
... Saved 120 files
... Saved 130 files
... Saved 140 files
... Saved 150 files
... Saved 160 files
... Saved 170 files
... Saved 180 files
... Saved 190 files
... Saved 200 files
... Saved 210 files
... Saved 220 files
... Saved 230 files
... Saved 240 files
... Saved 250 files
... Saved 260 files
... Saved 270 files
... Saved 280 files
... Saved 290 files
... Saved 300 files
... Saved 310 files
... Saved 320 files
... Saved 330 files
... Saved 340 files
... Saved 350 files
... Saved 360 files
... Saved 370 files
... Saved 380 files
... Saved 390 files
... Saved 400 files
... Saved 410 files
... Saved 420 files
... Saved 430 files
... Saved 440 files
... Saved 450 files
... Saved 460 files


2026-01-10 14:59:25.559505: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


... Saved 10 files
... Saved 20 files
... Saved 30 files
=== Converting Sand to individual .npz files ===
Output Directory: ./datasets/Sand/valid


2026-01-10 14:59:28.873522: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


... Saved 10 files
... Saved 20 files
... Saved 30 files


In [11]:
import matplotlib.pyplot as plt
from matplotlib import animation
from matplotlib import rc
import numpy as np

# 주피터 노트북 설정
rc('animation', html='jshtml')

In [16]:
def visualize_trajectory(dataset_name, split, trajectory_idx, skip_step=5):
    data_path = f'./datasets/{dataset_name}'
    loaded = np.load(os.path.join(data_path, split, f'trajectory_{trajectory_idx:04d}.npz'))
    
    pos_data = loaded['position']
    type_data = loaded['particle_type']
    
    num_steps = pos_data.shape[0]
    
    fig, ax = plt.subplots(figsize=(5, 5))
    ax.set_xlim(0, 1) 
    ax.set_ylim(0, 1)
    ax.set_aspect('equal')
    ax.grid(True, linestyle='--', alpha=0.3)
    ax.set_title(f"Scenario {trajectory_idx}")
    
    color_map = {
        3: "black",  # Boundary particles.
        0: "green",  # Rigid solids.
        7: "magenta",  # Goop.
        6: "gold",  # Sand.
        5: "blue",  # Water.
    }
    colors = [color_map.get(t, 'gray') for t in type_data]
    
    initial_pos = pos_data[0]
    scatter = ax.scatter(initial_pos[:, 0], initial_pos[:, 1], s=15, c=colors, alpha=0.7, edgecolors='none')
    
    def update(frame):
        current_pos = pos_data[frame]
        scatter.set_offsets(current_pos)
        ax.set_title(f"Step: {frame}/{num_steps}")
        return scatter,

    anim = animation.FuncAnimation(
        fig, update, frames=range(0, num_steps, skip_step), interval=30, blit=True
    )
    plt.close()
    return anim

In [15]:
# 실행
anim = visualize_trajectory('Sand', 'train', trajectory_idx=999, skip_step=5)
anim